In [1]:
%load_ext autoreload
%autoreload 2

# Experiments with WMF followed by context-aware model
First learn user and item factors with WMF (optimal hyperparams known) then learn context factors with CA model.

In [2]:
from pathlib import Path
from functools import partial

from tqdm.auto import tqdm

import src.io as io
import src.evaluation as evaluation
import src.evaluation.splits
import src.evaluation.cars

from src.algorithm.baseline.wmf import WMF
from src.algorithm.cars.itals import iTALS, iTALSs
from src.algorithm.cars.wtf import WTF
from src.algorithm.cars.italsx import iTALSx

## Datasets

In [3]:
DATA_DIR, RETARGET = Path('../../../data/CARS/TripAdvisor/'), False

In [4]:
# Shouldn't need to change this info
INTERACTIONS = DATA_DIR / 'interactions.csv'

SEED = 123456
SEED2 = 78910

ITEM_ID = 'item'
USER_ID = 'user'

MODELS = {
    'iTALS one': partial(iTALS, default_context_1=True, max_iterations=3),
    'iTALS': partial(iTALS, default_context_1=False, max_iterations=3),
    'iTALSs one': partial(iTALSs, default_context_1=True),
    'iTALSs': partial(iTALSs, default_context_1=False),
    'WTF one': partial(WTF, default_context_1=True, max_cg_iter=10),
    'WTF': partial(WTF, default_context_1=False, max_cg_iter=10),
    'iTALSx': iTALSx
}

## Provider of WMF factors for all models

In [5]:
K = 80
WMF_MAX_IT = 10

# depends on dataset
WMF_L2 = 1000
WMF_V = 0.25
WMF_ALPHA = 500

WMF_HYPERPARAMS = {'k': K, 'l2': WMF_L2, 'v': WMF_V, 'alpha': WMF_ALPHA, 'max_iterations': WMF_MAX_IT}

In [6]:
# map seed to learned factors
userItemFactorCache = dict()
def userItemFactorSupplier(data, seed):
    if seed not in userItemFactorCache:
        print("Computing factors WMF")
        wmf = WMF(**WMF_HYPERPARAMS)
        wmf.fit(data.toCSR())
        P, Q = wmf.getUserItemFactors()
        userItemFactorCache[seed] = (P, Q)
        
    return userItemFactorCache[seed]

## Define algorithm and hyperparameter ranges

In [7]:
L2 = [1, 10, 100, 1000, 10000]
V = [0, 0.25, 0.5, 0.75, 1]
ALPHA = [1, 10, 100, 1000, 10000]


HYPERPARAMS = {'k': K, 'l2': L2, 'v': V, 'alpha': ALPHA}
HYPERPARAMS

{'k': 80,
 'l2': [1, 10, 100, 1000, 10000],
 'v': [0, 0.25, 0.5, 0.75, 1],
 'alpha': [1, 10, 100, 1000, 10000]}

## Parse data

In [8]:
data = io.parse_interactions_with_context(INTERACTIONS, item_id=ITEM_ID, user_id=USER_ID)

## Make train/val split for hyperparam tuning

In [9]:
train, test = evaluation.splits.context_leave_one_out_split(data, seed=SEED)

## Perform gridsearch on validation set

In [10]:
P, Q = userItemFactorSupplier(train, SEED)

Computing factors WMF


  0%|          | 0/10 [00:00<?, ?it/s]

In [11]:
%%time
modelHyperparams = dict()
for modelName, Model in tqdm(MODELS.items()):
    score, bestHyperparams = evaluation.cars.gridsearchSetFactors(Model, train, test, P, Q, HYPERPARAMS, retarget=RETARGET)
    print(f"Best score of {score} for model {modelName} achieved with {bestHyperparams}.")
    modelHyperparams[modelName] = bestHyperparams

  0%|          | 0/7 [00:00<?, ?it/s]

  0%|          | 0/125 [00:00<?, ?it/s]

Training model <src.algorithm.cars.itals.iTALS object at 0x7f55d390b130> with hyperparameters {'k': 80, 'l2': 1, 'v': 0, 'alpha': 1}


  0%|          | 0/3 [00:00<?, ?it/s]

Evaluating with 2357 users
MRR@5 0.019
MRR@20 0.025
Average Recall@5 0.033
Average Recall@20 0.087
Training model <src.algorithm.cars.itals.iTALS object at 0x7f55d38ec0d0> with hyperparameters {'k': 80, 'l2': 10, 'v': 0, 'alpha': 1}


...

Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c3e2b820> with hyperparameters {'k': 80, 'l2': 1, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.014
MRR@20 0.017
Average Recall@5 0.027
Average Recall@20 0.061
Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c31fb5b0> with hyperparameters {'k': 80, 'l2': 10, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.014
MRR@20 0.018
Average Recall@5 0.028
Average Recall@20 0.062
Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c3960490> with hyperparameters {'k': 80, 'l2': 100, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.02
MRR@20 0.024
Average Recall@5 0.034
Average Recall@20 0.07
Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c3d95340> with hyperparameters {'k': 80, 'l2': 1000, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.023
MRR@20 0.028
Average Recall@5 0.038
Average Recall@20 0.085
Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c3ee7ac0> with hyperparam

  0%|          | 0/125 [00:00<?, ?it/s]

Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c3819e80> with hyperparameters {'k': 80, 'l2': 1, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.02
MRR@20 0.024
Average Recall@5 0.037
Average Recall@20 0.086
Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c3faa5e0> with hyperparameters {'k': 80, 'l2': 10, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.019
MRR@20 0.024
Average Recall@5 0.036
Average Recall@20 0.084
Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c3819040> with hyperparameters {'k': 80, 'l2': 100, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.021
MRR@20 0.026
Average Recall@5 0.036
Average Recall@20 0.09
Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c3473340> with hyperparameters {'k': 80, 'l2': 1000, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.023
MRR@20 0.029
Average Recall@5 0.045
Average Recall@20 0.109
Training model <src.algorithm.cars.wtf.WTF object at 0x7f55c3e58b80> with hyperparam

  0%|          | 0/125 [00:00<?, ?it/s]

Training model <src.algorithm.cars.italsx.iTALSx object at 0x7f55c319a970> with hyperparameters {'k': 80, 'l2': 1, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.025
MRR@20 0.029
Average Recall@5 0.048
Average Recall@20 0.101
Training model <src.algorithm.cars.italsx.iTALSx object at 0x7f55d00bc4c0> with hyperparameters {'k': 80, 'l2': 10, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.025
MRR@20 0.029
Average Recall@5 0.048
Average Recall@20 0.101
Training model <src.algorithm.cars.italsx.iTALSx object at 0x7f55d0122400> with hyperparameters {'k': 80, 'l2': 100, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.025
MRR@20 0.029
Average Recall@5 0.048
Average Recall@20 0.101
Training model <src.algorithm.cars.italsx.iTALSx object at 0x7f55c3b50190> with hyperparameters {'k': 80, 'l2': 1000, 'v': 0, 'alpha': 1}
Evaluating with 2357 users
MRR@5 0.025
MRR@20 0.03
Average Recall@5 0.048
Average Recall@20 0.101
Training model <src.algorithm.cars.italsx.iTALSx object at 

## Evaluate models with optimal hyperparams with KFolds Cross validation

In [12]:
%%time

for modelName, Model in MODELS.items():
    print()
    bestHyperparams = modelHyperparams[modelName]
    alg = Model(**bestHyperparams)
    results = evaluation.cars.contextKFoldsSetFactorsEval(alg, data, userItemFactorSupplier, nr_folds=5, seed=SEED2, retarget=RETARGET)
    print("Model:", modelName)
    print("Hyperparams:", bestHyperparams)
    evaluation.cars.printKfoldsMetrics(results)


Computing factors WMF


  0%|          | 0/10 [00:00<?, ?it/s]

  0%|          | 0/3 [00:00<?, ?it/s]

Evaluating with 2357 users
Computing factors WMF


  0%|          | 0/10 [00:00<?, ?it/s]

...

Evaluating with 2357 users


  0%|          | 0/10 [00:00<?, ?it/s]

Evaluating with 2357 users


  0%|          | 0/10 [00:00<?, ?it/s]

Evaluating with 2357 users
Model: iTALSs
Hyperparams: {'k': 80, 'l2': 1000, 'v': 0, 'alpha': 1000}
MRR@5 0.023 (0.003)
MRR@20 0.029 (0.002)
Average Recall@5 0.044 (0.004)
Average Recall@20 0.104 (0.007)

Evaluating with 2357 users
Evaluating with 2357 users
Evaluating with 2357 users
Evaluating with 2357 users
Evaluating with 2357 users
Model: WTF one
Hyperparams: {'k': 80, 'l2': 10, 'v': 0.75, 'alpha': 100}
MRR@5 0.025 (0.003)
MRR@20 0.03 (0.003)
Average Recall@5 0.045 (0.004)
Average Recall@20 0.106 (0.007)

Evaluating with 2357 users
Evaluating with 2357 users
Evaluating with 2357 users
Evaluating with 2357 users
Evaluating with 2357 users
Model: WTF
Hyperparams: {'k': 80, 'l2': 100, 'v': 0.25, 'alpha': 1000}
MRR@5 0.024 (0.003)
MRR@20 0.029 (0.003)
Average Recall@5 0.043 (0.004)
Average Recall@20 0.102 (0.008)

Evaluating with 2357 users
Evaluating with 2357 users
Evaluating with 2357 users
Evaluating with 2357 users
Evaluating with 2357 users
Model: iTALSx
Hyperparams: {'k': 80, '